# Method comparison
## Selection of dataset
scTensor utilized Tirosh et al human melanoma dataset to investigate interactions between non malignant cells. Here we will replicate this analysis using CellPhoneDB and scConnect.

In [1]:
import scanpy as sc
import scanpy.external as sce
import pandas as pd
import scConnect as cn
cn.database.version = "2020-5"
import numpy as np
import matplotlib

matplotlib.rcParams['pdf.fonttype'] = 42
matplotlib.rcParams['ps.fonttype'] = 42


# Human melanoma tumor Tirosh et al

In [2]:
df = pd.read_csv("../data/GSE72056_melanoma_single_cell_revised_v2.txt.gz", sep="\t", index_col=0)

In [3]:
x = df[3:]
meta = df[:3]
print(x.values.shape)
print(meta.shape)

(23686, 4645)
(3, 4645)


In [4]:
adata_h = sc.AnnData(X=x.T.values)

In [5]:
adata_h.var_names = x.index
adata_h.obs_names = x.columns

In [6]:
adata_h.obs = meta.T

In [7]:
adata_h.var_names_make_unique()
adata_h.obs_names_make_unique()

Convert transformed reads back to read counts.

In [8]:
# reads in log2(TPM/10+1)
adata_h.X = (np.exp2(adata_h.X)-1)*10

Map the annotated cell types to a new observation called "annotated"

In [9]:
cell_map={
    "0": "Malignant",
    "1": "T-cells",
    "2": "B-cells",
    "3": "Macrophages",
    "4": "Endothelial cells",
    "5": "CAF",
    "6": "NK"
}
adata_h.obs["annotated"] = [cell_map[str(int(cell_type))] for cell_type in adata_h.obs['non-malignant cell type (1=T,2=B,3=Macro.4=Endo.,5=CAF;6=NK)']]

### Remove malignant cells
Remove the malignant cells as done in the scTensor analysis.

In [10]:
adata_no_tumor = adata_h[[True if celltype not in ["Malignant"] else False for celltype in adata_h.obs["annotated"]]]

# Run scConnect

In [ ]:
# set databaes to contain all receptor types
cn.database.setup_database(organism="hsapiens")

In [11]:
adata_no_tumor = cn.genecall.meanExpression(adata_no_tumor, groupby="annotated", transformation=None, normalization=False, use_raw=False)

Trying to set attribute `.uns` of view, copying.


In [12]:
adata_no_tumor = cn.connect.ligands(adata_no_tumor, organism="hsapiens")
adata_no_tumor = cn.connect.receptors(adata_no_tumor, organism="hsapiens")

c:\users\jetja\anaconda3\envs\connect\lib\site-packages\scipy\stats\stats.py:402: RuntimeWarning: divide by zero encountered in log
  log_a = np.log(np.array(a, dtype=dtype))


In [ ]:
# Only run if changing settings, use load function instead
adata_no_tumor = cn.connect.specificity(
    adata_no_tumor, 
    n=1000, 
    groupby="annotated", 
    organism="hsapiens", 
    transformation=None,
    emperical=True,
    merge_dist=False)

In [ ]:
cn.connect.save_specificity(adata_no_tumor, "comparison/dumps/1000n_no_merge.xlsx")

In [13]:
cn.connect.load_specificity(adata_no_tumor, "comparison/dumps/1000n_no_merge.xlsx")

In [14]:
edges = cn.connect.interactions(adata_no_tumor, adata_no_tumor, self_reference=True, organism="hsapiens")
nodes = cn.connect.nodes(adata_no_tumor)

finding connections between 6 emitter clusters and 6 target clusters |██████████████████████████████| 100.0% 
precessing adata #1
processing cluster B-cells
processing cluster CAF
processing cluster Endothelial cells
processing cluster Macrophages
processing cluster NK
processing cluster T-cells


In [15]:
G = cn.graph.build_graph(edges, nodes)

Graph has 8950 interactions between 6 clusters
B-cells has 3735 interactions
CAF has 2705 interactions
Endothelial cells has 2284 interactions
Macrophages has 2899 interactions
NK has 1847 interactions
T-cells has 4430 interactions


In [19]:
from importlib import reload
cn.genecall = reload(cn.genecall)
cn.connect = reload(cn.connect)
cn.graph = reload(cn.graph)
cn.app = reload(cn.app)
cn.app.graph(G, mode="external", port="8070")

Dash app running on http://localhost:8888/proxy/8070/


# Export data to be used with cellPhoneDB

In [ ]:
df = adata_no_tumor.to_df().T
df.to_csv("cellPhoneDB/data.tsv", sep="\t")

In [ ]:
meta = adata_no_tumor.obs[["annotated"]]
meta.columns = ["cell_type"]
meta.to_csv("cellPhoneDB/meta.tsv", sep="\t")

## Script for CellPhoneDB analysis
### Initial analysis using statistical_analysis function:
`cellphonedb method statistical_analysis meta.tsv data.tsv --counts-data hgnc_symbol --pvalue 0.05 --iterations 1000 --threshold 0.1 --result-precision 5`

Note:
* iterations = 1000
* proportion expression threshold = 10%
* alpha = 0.05


## Plotting only significant interactions

As cellPhoneDB does not provide a way to filter out specific interactionson on the resulting dot_plot other than providing a manually currated list of connection and interactions , we will plot scConnect and CellPhoneDB results in a similar fashion from scratch.

The goal is to mimic CellPhoneDB's dotplot, and add some scConnect functionality, such as filtering on specificity and importance. CellPhoneDB dotplot plots -log(pval) (specificity) as the size and log(interaction score) as color.

### scConnect
The function bellow can plot all interactions where at least one interacton attribute is above a set threshold. Default is to filter all interactions that is specific (th = 1.3) between any two cell types. It is also possible to filter on importance to favor interactions where the interaction strenght is also prominent. We can further more change all ligand and receptor names to correponding human gene symbols, to make it easier to compare with CellPhoneDB.


In [36]:
import plotly.express as px
def interaction_edge_list(G, filter_by="specificity", th=1.3, cellphonedb_interactions=False, interaction_list=None):
    # lets plot all significant interactions
    import networkx as nx
    import plotly.express as px
    import pkg_resources
    version = "2019-5"
    organism = "hsapiens"
    
    df = nx.to_pandas_edgelist(G)
    
    # change name of scConnects interaction to better compare to cellPhoneDB
    receptor_info = pd.read_csv(pkg_resources.resource_filename("scConnect", (f"data/Gene_annotation/{version}/{organism}/receptors.csv")), index_col=1)
    ligand_info = pd.read_csv(pkg_resources.resource_filename("scConnect", (f"data/Gene_annotation/{version}/{organism}/ligands.csv")), index_col=1)

    df["ligand_gene"] = [eval(ligand_info.loc[ligand]["preprogene"])[0] if isinstance(ligand_info.loc[ligand]["preprogene"], str) else ligand for ligand in df["ligand"]]
    df["receptor_gene"] = [eval(receptor_info.loc[receptor]["gene"])[0] if isinstance(receptor_info.loc[receptor]["gene"], str) else receptor for receptor in df["receptor"]]

    df["cellphonedb_interactions"] = [f"{l}_{r}" for l, r in list(zip(df["ligand_gene"], df["receptor_gene"]))]

    #Create a new connection annotation merging source and target info
    df["connection"] = [str(connection[0]+"|"+connection[1]) for connection in zip(df["source"], df["target"])]

    # select all significant interaction (significance > 1)
    interactions = df[df[filter_by] >= th]["interaction"].unique()
    # keep all interactions that were significant between any connection
    df = df[[True if interaction in interactions else False for interaction in df["interaction"]]]

    # sort based on connection and interactoin names to get order in the plot
    if cellphonedb_interactions:
        df.sort_values(by=[ "cellphonedb_interactions", "connection"], key=np.vectorize(str.lower), ascending=False, inplace=True)
    else:
        df.sort_values(by=["connection", "interaction"], key=np.vectorize(str.lower), ascending=False, inplace=True)
    
    return df


def interaction_dotplot(G, df=None, filter_by="specificity", th=1.3, cellphonedb_interactions=False, height_scale=40, width_scale=40, cmap=px.colors.sequential.Viridis_r):
    import plotly.express as px
    
    if isinstance(df, pd.DataFrame):
        df = df
        # Filter by feature and threshold
        interactions = df[df[filter_by] >= th]["interaction"].unique()
        # keep all interactions that were significant between any connection
        df = df[[True if interaction in interactions else False for interaction in df["interaction"]]]
    else:
        df = interaction_edge_list(G, filter_by, th)
        
    # set width and hight of figure
    width = len(df["connection"].unique())*width_scale
    height = len(df["interaction"].unique())*height_scale
    if cellphonedb_interactions:
        y = "cellphonedb_interactions"
    else:
        y = "interaction"
    
    # log (specificity +1)for plotting size
    df["log_specificity"] = np.log10(df["specificity"]+1)
    
    # find and sort all connections
    connections = list(set(df["connection"]))
    connections.sort()

    
    
    plot = px.scatter(df, x="connection", y=y, 
        size="log_specificity", 
        color="log_score",
        opacity=0.8,
        height=height, width=width,
        size_max=10,
        template="plotly_white",
        render_mode="svg",
        title=f"Interactions with {filter_by} higher than {th}",
        color_continuous_scale=cmap,
        category_orders = {"connection": connections})
    
    plot.update_layout(coloraxis_colorbar=dict(
        title="Log score",
        thicknessmode="pixels", thickness = 20,
        lenmode="pixels", len=200,
        yanchor="top", y=1
        )
    )
    return plot
    

In [38]:
# Plot all interactions that have high specificity between two cell types
plot = interaction_dotplot(G, filter_by="specificity", th=1.3, cellphonedb_interactions=False, height_scale=25, width_scale=40)
plot.write_image("comparison/figures/scconnect_dotplot_all_specific.pdf")
plot.show()

### CellPhoneDB
Next, we want to replicate the above plotting function with the data produced by cellPhoneDB. We have access to the mean and p-values for each interaction, which we can use to mimic the results of scConnect. The pvalues represents the specificity of the interaction it self, compared to the ligand and receptor expression as in scConnect. We can calculate the -log(pval) to get the interaction specificity. Note that the significance threshold when doing this is 1.3, as -log(0.05) = 1.30. Unfortunatly cellPhoneDB returns p-values of 0, which should not be the case when using permutation (there is always one combination that can produce the observed values, hence the p-value can never be 0). To deal with this we scale the pvalues before transformation between values 10E-100 and 1 to mitiagete log(0). 

Note that the pvalues are not corrected for multiple testing, and not all tested interactions are reported from cellPhoneDB, we can hence not perform this correction. This will overestimate the number of specific interactions and make it impossible to filter out the interactinos with the highest specificity, as many small pvalues has been rounded to 0. e.i. th = 10 and th = 1.3 produce the same figure...



In [23]:
def cellphonedb_edge_list(path="cellPhoneDB/out/", filter_by="specificity", th=1.3):
    import pandas as pd
    import numpy as np
    import plotly.express as px
    
    # Load dataframes
    df_mean = pd.read_csv(path+"means.txt", sep="\t")
    df_pval = pd.read_csv(path+"pvalues.txt", sep="\t")
    df_mean.drop(columns=['id_cp_interaction', 'partner_a', 'partner_b',
       'gene_a', 'gene_b', 'secreted', 'receptor_a', 'receptor_b',
       'annotation_strategy', 'is_integrin'], inplace=True)
    df_pval.drop(columns=['id_cp_interaction', 'partner_a', 'partner_b',
       'gene_a', 'gene_b', 'secreted', 'receptor_a', 'receptor_b',
       'annotation_strategy', 'is_integrin'], inplace=True)
    df_mean.set_index(keys="interacting_pair", inplace=True)
    df_pval.set_index(keys="interacting_pair", inplace=True)

    # Create a interaction list (edge list) containing mean and pvalues                      
    interaction_list = list()
    for connection in df_mean.columns[1:]:
        for interaction in df_mean.index:
            record = [connection, interaction, df_mean.loc[interaction][connection], df_pval.loc[interaction][connection]]
            if isinstance(record[2], float):
                interaction_list.append(record)

    df = pd.DataFrame(interaction_list, columns=["connection", "interaction", "mean", "pval"])
    
    def scale(value, from_range=(0, 1), to_range=(10E-100, 1)): # mitagatelog with 0
        value = float(to_range[0] + (to_range[1] - to_range[0]) * (value -from_range[0]) / (to_range[1] - to_range[0]))
        return value
    
    df["pval"] = [scale(pval) for pval in df["pval"]] 
    # use same pvalue scaling as scConnect to unsure propper -log compatibility
    
    
    # Add nessesary attributes
    df["specificity"] = -np.log10(df["pval"])
    df["log_score"] = np.log10(df["mean"]+1)
    df["importance"] = df["specificity"] * df["log_score"]

    # Filter by feature and threshold
    interactions = df[df[filter_by] >= th]["interaction"].unique()
    # keep all interactions that were significant between any connection
    df = df[[True if interaction in interactions else False for interaction in df["interaction"]]]

    # sort based on connection and interactoin names to get order in the plot
    df.sort_values(by=[ "connection", "interaction"], key=np.vectorize(str.lower), ascending=False, inplace=True)
    return df
                          
def cellphonedb_dotplot(df=None, filter_by="specificity", th=1.3, path="cellPhoneDB/out/", height_scale=40, width_scale=40, cmap=px.colors.sequential.Viridis_r):
    import plotly.express as px
    # set width and hight of figure
    if isinstance(df, pd.DataFrame):
        df=df
        # Filter by feature and threshold
        interactions = df[df[filter_by] >= th]["interaction"].unique()
        # keep all interactions that were significant between any connection
        df = df[[True if interaction in interactions else False for interaction in df["interaction"]]]
    else:
        df = cellphonedb_edge_list(path, filter_by, th)
        
    width = len(df["connection"].unique())*width_scale
    height = len(df["interaction"].unique())*height_scale
    
    # log (specificity +1)for plotting size
    df["log_specificity"] = np.log10(df["specificity"]+1)
    
    # find and sort all connections
    connections = list(set(df["connection"]))
    connections.sort()
    
    plot = px.scatter(df, x="connection", y="interaction", 
        color="log_score",
        size = "log_specificity",
        opacity=0.8,
        height=height, width=width,
        size_max=10,
        template="plotly_white",
        render_mode="svg",
        title=f"Interactions with {filter_by} higher than {th}",
        color_continuous_scale=cmap,
        category_orders = {"connection": connections})
    
    plot.update_layout(coloraxis_colorbar=dict(
        title="Log score",
        thicknessmode="pixels", thickness = 20,
        lenmode="pixels", len=200,
        yanchor="top", y=1
        )
    )
    return plot
         

In [39]:
# plot all specific interactions
plot = cellphonedb_dotplot(filter_by="specificity", th=1.3, height_scale=20, width_scale=30)
plot.write_image("comparison/figures/cellphonedb_dotplot_all specific.pdf", scale=2)
plot.show()

## Detect incommon interactions
In order to detect interactions that both scConnect and CellPhoneDB identify, we must convert the protein names provided by scConnect to the correponding human gene symbols, as these are used by CellphoneDB to decribe interactions. Note however that scConnect does not have the heteromeric complexes that CellPhoneDB have, and that CellPhoneDB does not have the molecular ligands that scConnect have, so these interations will never be included.

We start by collecting all interactions detected as specific by both methods *(th 1.3 for scConnect and th 1.3 for CellPhoneDB)*

In [25]:
df_connect = interaction_edge_list(G, filter_by="specificity", th=1.3, cellphonedb_interactions=True)
df_cellphonedb = cellphonedb_edge_list(filter_by = "specificity", th=1.3)

Then we make a set of all interactions that are incommon and filter out only these interactions

In [26]:
cellphonedb_set = set([interaction for interaction in df_cellphonedb["interaction"]])
connect_set = set([interaction for interaction in df_connect["cellphonedb_interactions"]])
incommon = list(connect_set.intersection(cellphonedb_set))

df_connect = df_connect[[True if interaction in incommon else False for interaction in df_connect["cellphonedb_interactions"]]]
df_cellphonedb = df_cellphonedb[[True if interaction in incommon else False for interaction in df_cellphonedb["interaction"]]]

In [40]:
# plot all incommon interactions from scConnect
plot = interaction_dotplot(G=G, df=df_connect, filter_by="specificity", th=1, cellphonedb_interactions=True, height_scale=25, width_scale=30, cmap=px.colors.sequential.Reds)
plot.write_image("comparison/figures/scconnect_dotplot_incommon_1000.pdf")
plot.show()

In [41]:
# plot all incommon interactions from CellPhoneDB
plot = cellphonedb_dotplot(df=df_cellphonedb, th=1.3, filter_by="specificity", height_scale=32, width_scale=30, cmap=px.colors.sequential.Blues)
plot.write_image("comparison/figures/cellphonedb_dotplot_incommon_1000.pdf")
plot.show()

## Correlation of interaction strenght
scConnect and CellPhoneDB use the same underlying cell populations and gene expression profiles to estimate interaction strenght, althogh the exact method differ slightly. CellPhoneDB filter out receptor and ligands that are not expressed by more than a set proportion of the cell population (10% in our case). scConnect does not perform any such filtering. 

To test the correlation of interaction strenght between scConect and CellPhoneDB, we can plot the log score as reported by scConnect and by CellPhoneDB against each other.

In [29]:
# fetch all incommon interactions, change interaction names to gene symbols and index on connection and interaction
df_cn = df_connect[["connection", "cellphonedb_interactions", "log_score", "specificity"]].copy()
df_cn["interaction"] = df_cn["cellphonedb_interactions"]
df_cn.drop(columns=["cellphonedb_interactions"], inplace=True)
df_cn = df_cn.set_index(keys=["connection", "interaction"])

In [30]:
# Do the same for CellPhoneDB
df_cp = df_cellphonedb[["connection", "interaction", "log_score", "specificity"]]
df_cp = df_cp.set_index(keys=["connection", "interaction"])

In [31]:
# align both dataframes on the index
df_cn, df_cp = df_cn.align(df_cp, fill_value=0)


In [64]:
# Add the log score valeus from cellPhoneDB to the scConnect dataframe
df_cn["log_score_cp"] = df_cp["log_score"]
df_cn["specificity_cp"] = df_cp["specificity"]
df_cn

log_score  specificity  log_score_cp  \
connection      interaction                                          
B-cells|B-cells ANXA1_FPR1     0.515451    -0.000000      0.000000   
                ANXA1_FPR1     0.515451    -0.000000      0.000000   
                ANXA1_FPR3     0.222539    -0.000000      0.000000   
                C3_C3AR1       0.127484    -0.000000      0.000000   
                CCL21_CCR7     1.678505     0.297213      0.000000   
...                                 ...          ...           ...   
T-cells|T-cells TNF_TNFRSF1A   1.675327     0.129010      1.695896   
                TNF_TNFRSF1A   1.675327     0.129010      1.695896   
                TNF_TNFRSF1B   2.130988     0.606572      2.242314   
                VEGFA_FLT1     0.459197    -0.000000      0.749589   
                VEGFA_KDR      0.123170    -0.000000      0.125257   

                              specificity_cp  
connection      interaction                   
B-cells|B-cells ANXA1_FPR1          0.000000  
                ANXA1_FPR1          0.000000  
                ANXA1_FPR3          0.000000  
                C3_C3AR1            0.000000  
                CCL21_CCR7          0.000000  
...                                      ...  
T-cells|T-cells TNF_TNFRSF1A        0.106793  
                TNF_TNFRSF1A        0.106793  
                TNF_TNFRSF1B       99.000000  
                VEGFA_FLT1         -0.000000  
                VEGFA_KDR          -0.000000  

[1426 rows x 4 columns]

In [65]:
# plot CellPhoneDB vs. scConnect and add orinary least square regression line.
import plotly.express as px
plot = px.scatter(
    df_cn, x="log_score", y="log_score_cp", #marginal_x="violin", marginal_y="violin", 
    opacity=0.6, 
    trendline="ols",  trendline_color_override="red", 
    width=700, height=700, 
    labels=dict(
        log_score="scConnect Log Score",
        log_score_cp="cellPhoneDB Log Score"
    )
)
plot.write_image("comparison/figures/log_score_scatter.pdf", scale=10)
plot.show()

### Correlation summary
scConnect and cellPhoneDB interaction strength are quite similar, with cellPhoneDB on average reporting slighly higher interaction strengths. 

Some interactions by cellPhoneDB are 0, when scConnect reported them. These are most likely the populations with low participation (less than 10%) that were filtered out by cellPhoneDB (we set them to 0). 

CellPhoneDB calulates the mean of the ligand and receptor score to get an interaction score, and sets the interaction score to 0 if any of the ligand or receptor is 0. scConnect solves this by taking the geometric mean of the ligand and receptor score, which naturally apraches 0 as any ligand or receptor score apraches 0. This would explain the on average higher interaction estimation by cellPhoneDB.